In [ ]:
import os
# os.system('pip install openpyxl')
# os.system('pip install sentence-transformers')
import pandas as pd
import gradio as gr
from sentence_transformers import SentenceTransformer

model = SentenceTransformer('all-mpnet-base-v2') #all-MiniLM-L6-v2 #all-mpnet-base-v2

df = pd.read_parquet('df_encoded3.parquet')
df['tags'] = df['tags'].apply(lambda x : str(x))
def parse_raised(x):
    if x == 'Undisclosed':
        return 0
    else: 
        quantifier = x[-1]
        x = float(x[1:-1])
        if quantifier == 'K':
            return x/1000
        elif quantifier == 'M':
            return x
df['raised'] = df['raised'].apply(lambda x : parse_raised(x))
df['stage'] = df['stage'].apply(lambda x : x.lower())
df = df.reset_index(drop=True)

from sklearn.neighbors import NearestNeighbors
import pandas as pd
from sentence_transformers import SentenceTransformer

nbrs = NearestNeighbors(n_neighbors=5000, algorithm='ball_tree').fit(df['text_vector_'].values.tolist())

def search(df, query):
    product = model.encode(query).tolist()
    # product = df.iloc[0]['text_vector_'] #use one of the products as sample

    #prepare model
    # 
    distances, indices = nbrs.kneighbors([product]) #input the vector of the reference object

    #print out the description of every recommended product
    return df.iloc[list(indices)[0]][['name', 'raised', 'target', 'size', 'stage', 'country', 'source', 'description', 'tags']]

In [44]:
def filter_df(df, column_name, filter_type, filter_value, minimum_acceptable_size=0):
    if filter_type == '==':
        df_filtered = df[df[column_name]==filter_value]
    elif filter_type == '>=':
        df_filtered = df[df[column_name]>=filter_value]
    elif filter_type == '<=':
        df_filtered = df[df[column_name]<=filter_value]
    elif filter_type == 'contains':
        df_filtered = df[df['target'].str.contains(filter_value)]

    if df_filtered.size >= minimum_acceptable_size:
        return df_filtered
    else:
        return df

#the first module becomes text1, the second module file1
def greet(size, target, stage, query): 
    def raised_zero(x):
        if x == 0:
            return 'Undisclosed'
        else:
            return x
    df_knn = search(df, query)
    #we live the sorting for last
    df_knn = df_knn.sort_values('raised', ascending=False)
    df_knn['raised'] = df_knn['raised'].apply(lambda x : raised_zero(x))

    df_size = filter_df(df_knn, 'size', '==', size, 1000)
    df_target = filter_df(df_size, 'target', 'contains', target, 20)
    df_stage = filter_df(df_target, 'stage', '==', stage.lower(), 10)
    
    display(df_stage)
    # df_raised = df_target[(df_target['raised'] >= raised) | (df_target['raised'] == 0)]

    return df_stage[0:100]

with gr.Blocks(theme=gr.themes.Soft(primary_hue='amber', secondary_hue='gray', neutral_hue='amber')) as demo:
    gr.Markdown(
    """
    # Startup Search Engine
    """
    )
    size = gr.Radio(['1-10', '11-50', '51-200', '201-500', '500+', '11-500+'], multiselect=False, value='11-500+', label='size')
    target = gr.Radio(['B2B', 'B2C', 'B2G', 'B2B2C'], multiselect=False, value='B2B', label='target')
    stage = gr.Radio(['pre-seed', 'A', 'B', 'C', 'exit'], multiselect=False, value='C', label='stage')
    # raised = gr.Slider(0, 20, value=5, step_size=1, label="Minimum raising (in Millions)")
    query = gr.Textbox(label='Describe the Startup you are searching for', value='age reversing')
    btn = gr.Button(value="Search for a Startup")
    output1 = gr.DataFrame(label='value')
    # btn.click(greet, inputs='text', outputs=['dataframe'])
    btn.click(greet, [size, target, stage, query], [output1])
demo.launch(share=False)

c:\Users\ardit\AppData\Local\Programs\Python\Python39\lib\site-packages\gradio\deprecation.py:43: UserWarning: You have unused kwarg parameters in Radio, please remove them: {'multiselect': False}
  warnings.warn(


Running on local URL:  http://127.0.0.1:7884

To create a public link, set `share=True` in `launch()`.


name       raised       target     size stage  \
78931    Developeration  Undisclosed  Undisclosed  11-500+     c   
77566   ComplyAdvantage  Undisclosed  Undisclosed  11-500+     c   
78674             Atlas  Undisclosed  Undisclosed  11-500+     c   
81682  48 Factoring Inc  Undisclosed  Undisclosed  11-500+     c   
78926             Xinca  Undisclosed  Undisclosed  11-500+     c   
...                 ...          ...          ...      ...   ...   
80432              Glow  Undisclosed  Undisclosed  11-500+     c   
77716             Owiwi  Undisclosed  Undisclosed  11-500+     c   
78561           Quantib  Undisclosed  Undisclosed  11-500+     c   
77554            Earnin  Undisclosed  Undisclosed  11-500+     c   
80694    Vibrent Health  Undisclosed  Undisclosed  11-500+     c   

               country                        source  \
78931           sweden  https://www.startupblink.com   
77566   united-kingdom  https://www.startupblink.com   
78674           russia  https://www.startupblink.com   
81682    united-states  https://www.startupblink.com   
78926        argentina  https://www.startupblink.com   
...                ...                           ...   
80432            china  https://www.startupblink.com   
77716           greece  https://www.startupblink.com   
78561  the-netherlands  https://www.startupblink.com   
77554    united-states  https://www.startupblink.com   
80694    united-states  https://www.startupblink.com   

                                             description  \
78931  Developeration AB was founded 2016 and is a st...   
77566  We are a financial crime solutions provider co...   
78674  Atlas Biomedical Holding is developing a netwo...   
81682  48 Factoring Inc. is a financial services comp...   
78926  Incorporar residuos en la fabricaci&oacute;n d...   
...                                                  ...   
80432  Glow is an ambitious enterprise that uniquely ...   
77716  Owiwi is a fun and engaging psychometric tool ...   
78561  MRI scan technology to better diagnose -- and ...   
77554  We're building a platform of community-support...   
80694  The future of developing new cures for patient...   

                           tags  
78931            ['healthtech']  
77566               ['fintech']  
78674            ['healthtech']  
81682               ['fintech']  
78926  ['energy' 'environment']  
...                         ...  
80432            ['healthtech']  
77716       ['software' 'data']  
78561            ['healthtech']  
77554               ['fintech']  
80694            ['healthtech']  

[94 rows x 9 columns]

In [ ]:
# Define database of sentences
sentences = pd.Series(['The quick brown fox jumps over the lazy dog',
                       'A quick brown dog jumps over the lazy fox',
                       'The lazy dog jumps over the quick brown fox',
                       'The quick brown fox jumps over the lazy cat',
                       'The quick brown cat jumps over the lazy dog'])

# Encode sentences
sentence_embeddings = model.encode(sentences)

# Define query sentence
query = 'A lazy dog jumps over the quick brown fox'

# Encode query
query_embedding = model.encode(query)

# Search for similar sentences
cosine_scores = util.pytorch_cos_sim(query_embedding, sentence_embeddings)
most_similar_sentence = sentences[cosine_scores.argmax()]